In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
import json
from time import sleep
import nltk
import numpy as np
import argparse
from langchain.llms import OpenAI
from langchain.chat_models import ChatOpenAI
from langchain.schema import AIMessage, HumanMessage, SystemMessage
from langchain.prompts import HumanMessagePromptTemplate
from src.baselines.baseline_utils import load_jsonl, run_model, run_baseline, OpenAIWrapper, create_prompt_template
from dotenv import load_dotenv
from types import SimpleNamespace
import asyncio
load_dotenv('src/baselines/.env')

/home/d_wang/anaconda3/envs/maf/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


True

In [3]:
args = {
    'data_dir': 'data/entailment_data/partitions',
    'save_dir': 'src/baselines/models',
    'debug': False,
    'exp_label': 'default',
    'task': 'entailment_baseline',
    'model': 'gpt-3.5-turbo',
    'prompting_technique': '3shot_entailment',
    'max_tokens': 2048,
    'temperature': 0.0,
}
args = SimpleNamespace(**args)

In [4]:
os.getcwd()


'/home/d_wang/nlp/MAF'

In [5]:
def format_entailment_prompt(context, hypothesis):
    return f'Hypothesis: {hypothesis}\n\nText:\n{context}\n\n'

In [20]:
async def baseline(model, prompt_technique, model_name):
    prompt_template = create_prompt_template('entailment_baseline', 'gpt-3.5-turbo', '3shot_entailment')
    for task in ['task_1', 'task_2']:
        data = load_jsonl(f'data/entailment_data/data/public_dataset/entailment_trees_emnlp2021_data_v2/dataset/{task}/dev.jsonl')
        for i in range(len(data)):
            data[i]['input'] = format_entailment_prompt(data[i]['context'], data[i]['hypothesis'])
        print(data)
        output_file  = f'src/baselines/models/{model_name}/{prompt_technique}/{task}_results.json'
        if (os.path.exists(output_file)):
            continue
        output_folder = f'src/baselines/models/{model_name}/{prompt_technique}'
        if (not os.path.exists(output_folder)):
            os.makedirs(output_folder)
        data = await run_model(model, prompt_template, data, output_file=output_file)
        with open(output_file, 'w') as f:
            f.write(json.dumps(data) + '\n')
            

In [7]:
test = ChatOpenAI(
    model_name=args.model, 
    max_tokens=args.max_tokens, 
    temperature=args.temperature,
    openai_api_key = os.getenv('OPENAI_API_KEY')
)

In [15]:
await test.agenerate([[HumanMessage(content='hi')]])

LLMResult(generations=[[ChatGeneration(text='Hello! How can I assist you today?', generation_info=None, message=AIMessage(content='Hello! How can I assist you today?', additional_kwargs={}, example=False))]], llm_output={'token_usage': {'prompt_tokens': 9, 'completion_tokens': 9, 'total_tokens': 18}, 'model_name': 'gpt-3.5-turbo'})

In [8]:
gpt3 = OpenAIWrapper(
    model_name=args.model, 
    max_tokens=args.max_tokens, 
    temperature=args.temperature,
    openai_api_key = os.getenv('OPENAI_API_KEY')
)

In [9]:
await gpt3(['hi'])

[[HumanMessage(content='hi', additional_kwargs={}, example=False)]]


['Hello! How can I assist you today?']

In [9]:
await gpt3('hi')

Got unknown type h
API server overloaded. Waiting for 30 seconds...


In [ ]:
davinci = OpenAIWrapper(
    model_name='text-davinci-003',
    max_tokens=args.max_tokens, 
    temperature=args.temperature,
    openai_api_key = os.getenv('OPENAI_API_KEY')
)

In [21]:
await baseline(gpt3, args.prompting_technique, args.model)

[{'id': 'Mercury_SC_401371', 'context': 'sent1: the sun rising / setting occurs once per day sent2: the sun setting is a kind of event sent3: the sun rising is a kind of event', 'question': 'Which event occurs on a daily cycle?', 'answer': 'The Sun rises and sets.', 'hypothesis': 'the sun rising and setting is the event that occurs once per day', 'proof': 'sent1 & sent2 & sent3 -> hypothesis; ', 'full_text_proof': ' [BECAUSE] the sun rising / setting occurs once per day [AND] the sun setting is a kind of event [AND] the sun rising is a kind of event [INFER] int1: the sun rising and setting is the event that occurs once per day', 'depth_of_proof': 1, 'length_of_proof': 1, 'meta': {'question_text': 'Which event occurs on a daily cycle?', 'answer_text': 'The Sun rises and sets.', 'hypothesis_id': 'int1', 'triples': {'sent1': 'the sun rising / setting occurs once per day', 'sent2': 'the sun setting is a kind of event', 'sent3': 'the sun rising is a kind of event'}, 'distractors': [], 'dist

Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 1.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limit: 90000 / min. Current: 89092 / min. Contact us through our help center at help.openai.com if you continue to have issues..


Completed 70 problems
[[HumanMessage(content='A chat between a curious human and an artificial intelligence assistant. The human gives a hypothesis along with a set of sentences that includes sentences which entail the hypothesis. The AI assistant then generates a tree of entailments that shows how the hypothesis can be entailed from the given sentences.\n\nUSER:\nHypothesis: Eruptions can cause plants to die\n\nText:\n# sent 1: eruptions emit lava\n# sent 2: plants have green leaves\n# sent 3: eruptions produce ash clouds\n# sent 4: producers will die without sunlight\n# sent 5: ash blocks sunlight\n\nASSISTANT:\nEntailment Tree:\nsent 3 and sent 5: eruptions produce ash clouds and ash blocks sunlight -> int 1: eruptions block sunlight\nsent 4 and int 1: producers will die without sunlight and eruptions block sunlight -> H: Eruptions can cause plants to die\n\n### END ###\n\nUSER:\nHypothesis: An astronaut requires the oxygen in a spacesuit backpack to breathe\n\nText:\n# sent 1: spac

Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 2.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limit: 90000 / min. Current: 87490 / min. Contact us through our help center at help.openai.com if you continue to have issues..
Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 1.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limit: 90000 / min. Current: 87260 / min. Contact us through our help center at help.openai.com if you continue to have issues..
Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 1.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limi

Completed 75 problems
[[HumanMessage(content='A chat between a curious human and an artificial intelligence assistant. The human gives a hypothesis along with a set of sentences that includes sentences which entail the hypothesis. The AI assistant then generates a tree of entailments that shows how the hypothesis can be entailed from the given sentences.\n\nUSER:\nHypothesis: Eruptions can cause plants to die\n\nText:\n# sent 1: eruptions emit lava\n# sent 2: plants have green leaves\n# sent 3: eruptions produce ash clouds\n# sent 4: producers will die without sunlight\n# sent 5: ash blocks sunlight\n\nASSISTANT:\nEntailment Tree:\nsent 3 and sent 5: eruptions produce ash clouds and ash blocks sunlight -> int 1: eruptions block sunlight\nsent 4 and int 1: producers will die without sunlight and eruptions block sunlight -> H: Eruptions can cause plants to die\n\n### END ###\n\nUSER:\nHypothesis: An astronaut requires the oxygen in a spacesuit backpack to breathe\n\nText:\n# sent 1: spac

...

Completed 185 problems
[[HumanMessage(content='A chat between a curious human and an artificial intelligence assistant. The human gives a hypothesis along with a set of sentences that includes sentences which entail the hypothesis. The AI assistant then generates a tree of entailments that shows how the hypothesis can be entailed from the given sentences.\n\nUSER:\nHypothesis: Eruptions can cause plants to die\n\nText:\n# sent 1: eruptions emit lava\n# sent 2: plants have green leaves\n# sent 3: eruptions produce ash clouds\n# sent 4: producers will die without sunlight\n# sent 5: ash blocks sunlight\n\nASSISTANT:\nEntailment Tree:\nsent 3 and sent 5: eruptions produce ash clouds and ash blocks sunlight -> int 1: eruptions block sunlight\nsent 4 and int 1: producers will die without sunlight and eruptions block sunlight -> H: Eruptions can cause plants to die\n\n### END ###\n\nUSER:\nHypothesis: An astronaut requires the oxygen in a spacesuit backpack to breathe\n\nText:\n# sent 1: spa

Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 1.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limit: 90000 / min. Current: 87242 / min. Contact us through our help center at help.openai.com if you continue to have issues..
Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 1.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limit: 90000 / min. Current: 87242 / min. Contact us through our help center at help.openai.com if you continue to have issues..
Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 1.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limi

Completed 190 problems
[{'id': 'Mercury_SC_401371', 'context': 'sent1: increasing is a kind of order sent2: the sunlight occurs during the day sent3: days ( d ) are a metric unit used for measuring time generally used for values between 1 and 365 sent4: the sun setting is a kind of event sent5: temperature rise means temperature increase sent6: a revolution occurs when something revolves around something else sent7: being in the sun is synonymous with being in the sunlight sent8: everyday means daily sent9: the afternoon is a part of the day sent10: the sun rising / setting occurs once per day sent11: daytime means day sent12: the sun rising is a kind of event sent13: temperature rise means become warmer sent14: the day time is part of one day sent15: to happen means to occur sent16: motion / movement means moving / to move sent17: days are a kind of unit for measuring time sent18: afternoon is a part of day time sent19: rising means elevation sent20: month is a kind of period of time 

Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 2.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limit: 90000 / min. Current: 88758 / min. Contact us through our help center at help.openai.com if you continue to have issues..
Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 2.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limit: 90000 / min. Current: 88734 / min. Contact us through our help center at help.openai.com if you continue to have issues..
Retrying langchain.chat_models.openai.acompletion_with_retry.<locals>._completion_with_retry in 4.0 seconds as it raised RateLimitError: Rate limit reached for default-gpt-3.5-turbo in organization org-UL2nM4hjGA7CzFPYucOtFrPC on tokens per min. Limi

ASSISTANT:
Entailment Tree:
sent3 and sent8: days are a metric unit used for measuring time generally used for values between 1 and 365 and everyday means daily -> int1: a day occurs every day
sent10 and int1: the sun rising / setting occurs once per day and a day occurs every day -> H: the sun rising and setting is the event that occurs once per day

### END ###
Completed 5 problems
[[HumanMessage(content='A chat between a curious human and an artificial intelligence assistant. The human gives a hypothesis along with a set of sentences that includes sentences which entail the hypothesis. The AI assistant then generates a tree of entailments that shows how the hypothesis can be entailed from the given sentences.\n\nUSER:\nHypothesis: Eruptions can cause plants to die\n\nText:\n# sent 1: eruptions emit lava\n# sent 2: plants have green leaves\n# sent 3: eruptions produce ash clouds\n# sent 4: producers will die without sunlight\n# sent 5: ash blocks sunlight\n\nASSISTANT:\nEntailment Tr